# Hyper parameter search for CQL

In [10]:
!pip install d3rlpy

In [11]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import itertools
import math
import subprocess
import os
import d3rlpy
# plt.style.use('matplotlibrc')

# from Python.data_sampler import *

## Building an MDPDataset

We first read in a large batch of samples from the file. As `d3rlpy` wants it in the form (observations, actions, rewards, terminal flags), we go ahead and do that. Here's a helper function to get a dataset from a list of chunks of your choosing.

In [12]:
import numpy as np
import torch
import random
import pandas
from Python.data_sampler import *

In [13]:
def get_dataset(chunks : list, batch_size=30000, 
                path="collected_data/rl_det_small.txt") -> d3rlpy.dataset.MDPDataset :
    random.seed(0)
    samples = DataSampler(path_to_data=path)
    samples.setting("coarse")
    states = []
    actions = []
    rewards = []
    next_states = []
    for chunk in chunks:
        samples.use_chunk(chunk)
        samples.read_chunk()
        [statesChunk, actionsChunk, rewardsChunk, nextStatesChunk] = samples.get_batch(batch_size)
        states.append(statesChunk)
        actions.append(actionsChunk)
        rewards.append(rewardsChunk)
        next_states.append(nextStatesChunk)
    states = torch.cat(states)
    actions = torch.cat(actions)
    rewards = torch.cat(rewards)
    next_states = torch.cat(next_states)
    terminals = np.zeros(len(states))
    terminals[::1111] = 1 #episode length 100, change if necessary
    print(states.shape)
    dataset = d3rlpy.dataset.MDPDataset(states.numpy(), 
                                        actions.numpy(), 
                                        rewards.numpy(), terminals)
    return dataset, states.numpy(), actions.numpy(), rewards.numpy()

We can build the dataset from there, just like this, and split into train and test sets.

In [14]:
dataset, states, actions, rewards = get_dataset([i+200 for  i in range(100)], path="../collected_data/rl_stochpid.txt")

start
[ 0.00000000e+00  7.95731469e+08 -2.55189108e-01  2.54000047e-02
  2.57999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.30457556e-01 -3.26640595e-01  6.00000000e-01]
Read chunk # 201 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.22789108e-01 -1.71999953e-02
  2.39998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.18067885e-01 -4.36092621e-01  6.00000000e-01]
Read chunk # 202 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.89891077e-02  1.38000047e-02
  1.55999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  6.00000000e-01 -5.13215135e-01  3.00794900e-01]
Read chunk # 203 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  4.39310892e-01 -5.61999953e-02
 -4.10001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.81283783e-02  6.00000000e-01 -6.00000000e-01]
Read chunk # 204 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.02089108e-01  1.38000047e-02
  2.84999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.

[ 0.00000000e+00  7.95731469e+08 -2.86689108e-01  3.36000047e-02
 -8.80001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -4.83419307e-01 -6.00000000e-01  6.00000000e-01]
Read chunk # 247 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -4.29489108e-01  1.24000047e-02
  1.97999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.73149828e-01 -6.00000000e-01  6.00000000e-01]
Read chunk # 248 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  5.92108923e-02 -1.15999953e-02
 -2.20001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.12672481e-02  1.26197128e-01 -4.51488887e-01]
Read chunk # 249 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  2.47108923e-02  5.20000047e-02
  1.82999866e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  3.92298179e-01  4.75144083e-03 -9.25660004e-02]
Read chunk # 250 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.79989108e-01  2.20000469e-03
 -1.09000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -1.569924

[ 0.00000000e+00  7.95731469e+08 -3.04389108e-01  5.24000047e-02
 -2.83000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -6.00000000e-01 -6.00000000e-01  6.00000000e-01]
Read chunk # 293 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -1.79889108e-01 -2.13999953e-02
 -8.00001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -1.48109576e-01 -6.00000000e-01  6.00000000e-01]
Read chunk # 294 out of 4999
start
[ 0.00000000e+00  7.95731469e+08  4.24108923e-02 -5.33999953e-02
  6.69998658e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
  4.81836613e-01  3.10953755e-01 -6.00000000e-01]
Read chunk # 295 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -3.41289108e-01  3.60000047e-02
 -1.40001342e-03  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -8.27789575e-02 -6.00000000e-01  6.00000000e-01]
Read chunk # 296 out of 4999
start
[ 0.00000000e+00  7.95731469e+08 -2.38689108e-01 -5.93999953e-02
 -1.91000134e-02  0.00000000e+00 -5.33423489e+00 -1.57091618e+00
 -5.347818

In [15]:
print("The behavior policy value statistics are:")
dataset.compute_stats()['return']

The behavior policy value statistics are:


{'mean': -116.6173,
 'std': 91.33919,
 'min': -391.5658,
 'max': 0.0,
 'histogram': (array([ 3,  2,  2,  1,  0,  2,  0,  3,  1,  2,  3,  3,  3,  5,  7, 16, 22,
         21,  3,  1]),
  array([-391.5658  , -371.98752 , -352.4092  , -332.83093 , -313.25262 ,
         -293.67435 , -274.09607 , -254.51776 , -234.93948 , -215.36119 ,
         -195.7829  , -176.2046  , -156.62631 , -137.04803 , -117.46974 ,
          -97.89145 ,  -78.313156,  -58.73487 ,  -39.156578,  -19.578289,
            0.      ], dtype=float32))}

In [16]:
from sklearn.model_selection import train_test_split
train_episodes, test_episodes = train_test_split(dataset, test_size=0.2)

## Setting up an Algorithm

In [17]:
from d3rlpy.algos import CQL
from d3rlpy.models.encoders import VectorEncoderFactory

from d3rlpy.preprocessing import MinMaxActionScaler
import random
action_scaler = MinMaxActionScaler(minimum=-0.6, maximum=0.6)

from d3rlpy.metrics.scorer import td_error_scorer
from d3rlpy.metrics.scorer import average_value_estimation_scorer
from d3rlpy.metrics.scorer import initial_state_value_estimation_scorer

from d3rlpy.ope import FQE
# metrics to evaluate with
from d3rlpy.metrics.scorer import soft_opc_scorer
import pickle as pkl
from statistics import harmonic_mean as hm

## Perform a random search on hyper params. 

As good fqe on both stochastic and deterministic data is needed for good performance during the evaluation step in the simulator, we take the harmonic mean of both fqes to understand the performance on each dataset. The harmonic mean is large only when each number whose mean is being taken is large. Therefore, a large harmonic mean corresponds to large numbers whose mean is being taken.


In [18]:

# The number of times we would wanna do a random search for hyper-params. In 
# every random search, we randomly pick a new set of hyper-params.
num_search_iterations = 40
largest_fqe = -np.inf

for i in range(num_search_iterations):

    random.seed()

    actor_lr_this_iter = random.uniform(1e-5, 1e-2)
    critic_lr_this_iter = random.uniform(1e-5, 1e-2)
    temp_lr_this_iter = random.uniform(1e-5, 1e-4)
    n_steps_this_iter = random.choice([1, 3, 5, 7])

    actor_encoder = VectorEncoderFactory(hidden_units=[12, 24, 36, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)
    critic_encoder = VectorEncoderFactory(hidden_units=[12, 24, 24, 12],
                                          activation='relu', use_batch_norm=True, dropout_rate=0.2)

    print("search iteration: ", i)
    print("using hyper params: ", [actor_lr_this_iter, critic_lr_this_iter, 
                                   temp_lr_this_iter, n_steps_this_iter])

    model = CQL(q_func_factory='qr', #qr -> quantile regression q function, but you don't have to use this
                reward_scaler='standard',
#                 actor_encoder_factory = actor_encoder,
#                 critic_encoder_factory = critic_encoder,
                action_scaler=action_scaler,
                actor_learning_rate=actor_lr_this_iter, 
                critic_learning_rate=critic_lr_this_iter,
                temp_learning_rate=temp_lr_this_iter,
                n_steps=n_steps_this_iter, 
                use_gpu=True) #change it to true if you have one
    model.build_with_dataset(dataset)

    model.fit(train_episodes,
        eval_episodes=test_episodes,
        n_epochs=50, 
        tensorboard_dir='runs',
        scorers={
            'td_error': td_error_scorer,
            'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i+1000 for i  in range(20)], 
                                                                    path="../collected_data/rl_stochpid.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_stoch = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    ope_dataset, states_ope, actions_ope, rewards_ope = get_dataset([i for i in range(40)], 
                                                                    path="../collected_data/rl_purestochastic.txt") #change if you'd prefer different chunks
    ope_train_episodes, ope_test_episodes = train_test_split(ope_dataset, test_size=0.2)

    fqe = FQE(algo=model, action_scaler = action_scaler, use_gpu=True) #change this if you have one!
    history_det = fqe.fit(ope_train_episodes,
        eval_episodes=ope_test_episodes,
        tensorboard_dir='runs',
        n_epochs=50, n_steps_per_epoch=1000, #change if overfitting/underfitting
        scorers={
           'init_value': initial_state_value_estimation_scorer,
            'ave_value': average_value_estimation_scorer,
           'soft_opc': soft_opc_scorer(return_threshold=0)
        })
    
    if(hm([history_stoch[-1][1]["ave_value"] + 50, 
           history_det[-1][1]["ave_value"] + 50]) \
                                                          > largest_fqe):
        largest_fqe = hm([history_stoch[-1][1]["ave_value"] + 50, 
                         history_det[-1][1]["ave_value"] + 50])

        # Save the hyper-params
        hyperparams = [actor_lr_this_iter, critic_lr_this_iter, 
                       temp_lr_this_iter, n_steps_this_iter]

        with open("hyperparams_cql.pkl", "wb") as f:
            print("most optimal hyper params for cql at this point: ", hyperparams)
            pkl.dump(hyperparams, f)

        # Save model and policy
        model.save_model("model_hyperparams_cql.pt")
        model.save_policy("policy_hyperparams_cql.pt")


search iteration:  0
using hyper params:  [0.0006716406409940611, 0.002206817187940385, 3.919949661777032e-05, 3]
2022-04-20 15:25.34 [debug    ] RoundIterator is selected.
2022-04-20 15:25.34 [info     ] Directory is created at d3rlpy_logs/CQL_20220420152534
2022-04-20 15:25.34 [debug    ] Fitting action scaler...       action_scaler=min_max
2022-04-20 15:25.34 [debug    ] Fitting reward scaler...       reward_scaler=standard
2022-04-20 15:25.34 [warning  ] Skip building models since they're already built.
2022-04-20 15:25.34 [info     ] Parameters are saved to d3rlpy_logs/CQL_20220420152534/params.json params={'action_scaler': {'type': 'min_max', 'params': {'minimum': array(-0.6), 'maximum': array(0.6)}}, 'actor_encoder_factory': {'type': 'default', 'params': {'activation': 'relu', 'use_batch_norm': False, 'dropout_rate': None}}, 'actor_learning_rate': 0.0006716406409940611, 'actor_optim_factory': {'optim_cls': 'Adam', 'betas': (0.9, 0.999), 'eps': 1e-08, 'weight_decay': 0, 'amsgrad'

Epoch 1/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-20 15:25.38 [info     ] CQL_20220420152534: epoch=1 step=342 epoch=1 metrics={'time_sample_batch': 0.00022835341113352635, 'time_algorithm_update': 0.012206148682979116, 'temp_loss': 4.719915053997821, 'temp': 0.99341635048738, 'alpha_loss': -16.46600731911018, 'alpha': 1.0170674822483843, 'critic_loss': 35.16187782176057, 'actor_loss': 0.8886321296830993, 'time_step': 0.012485552949515002, 'td_error': 2.3450674034916914, 'init_value': -3.6558213233947754, 'ave_value': -2.34637335012927} step=342
2022-04-20 15:25.39 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220420152534/model_342.pt


Epoch 2/50:   0%|          | 0/342 [00:00<?, ?it/s]

2022-04-20 15:25.43 [info     ] CQL_20220420152534: epoch=2 step=684 epoch=2 metrics={'time_sample_batch': 0.00025492802000882334, 'time_algorithm_update': 0.01094192649885925, 'temp_loss': 4.491180210782771, 'temp': 0.9805451138326299, 'alpha_loss': -11.177298913922225, 'alpha': 1.047189322131419, 'critic_loss': 21.19385628393519, 'actor_loss': 3.37152078590895, 'time_step': 0.011250973444933083, 'td_error': 3.958677795854501, 'init_value': -9.645764350891113, 'ave_value': -5.0735166328564825} step=684
2022-04-20 15:25.43 [info     ] Model parameters are saved to d3rlpy_logs/CQL_20220420152534/model_684.pt


...

2022-04-20 20:49.44 [info     ] FQE_20220420204902: epoch=49 step=16856 epoch=49 metrics={'time_sample_batch': 0.0001530917577965315, 'time_algorithm_update': 0.0020502570063568827, 'loss': 0.511474343514893, 'time_step': 0.002274059972097707, 'init_value': -20.974571228027344, 'ave_value': -27.78835693087664, 'soft_opc': nan} step=16856


2022-04-20 20:49.44 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220420204902/model_16856.pt


Epoch 50/50:   0%|          | 0/344 [00:00<?, ?it/s]

2022-04-20 20:49.45 [info     ] FQE_20220420204902: epoch=50 step=17200 epoch=50 metrics={'time_sample_batch': 0.00015653427257094273, 'time_algorithm_update': 0.0020980966645617817, 'loss': 0.5384062088885193, 'time_step': 0.0023267393888429153, 'init_value': -21.142227172851562, 'ave_value': -27.81341360630216, 'soft_opc': nan} step=17200


2022-04-20 20:49.45 [info     ] Model parameters are saved to d3rlpy_logs/FQE_20220420204902/model_17200.pt


## Reading hyper params from file

In [19]:
with open("hyperparams_cql.pkl", "rb") as f:
    data = pkl.load(f)

print(data)

[0.0008288831520532805, 0.003934260713329634, 4.6195344911552404e-05, 7]
